# **Functions to compute the dGLI coordinates**


***Imports***

In [1]:
import numpy as np
from numpy.linalg import norm

***dGLI functions***









In [2]:
# curve as the mesh border
def getdGLICoords(curve, sideSize):
    #corners = (0, 19, 38, 57)
    corners=[0, sideSize-1, 2*sideSize - 2, 3*sideSize - 3]
    subCurveEdges=selectedEdges(curve, corners)
    return dGLICoords(subCurveEdges)

def selectedEdges(curve, cornersInd):
    selEdgesInd = []
    outCurve = []
    # If curve is not closed (ie, first and initisl point are not the same) we close it in order to consider also the last segment
    if curve[0] != curve[-1]:
        curve.append(curve[0])
   
    # for each corner we consider the two edges of both sides   
    for ind in cornersInd:
        selEdgesInd.append(subtractCircularBeg(len(curve), ind))
        selEdgesInd.append([ind+2, ind+3])
       
    #selEdgesInd = sorted(selEdgesInd)
    for e in selEdgesInd:
        outCurve.append([curve[e[0]], curve[e[1]]])
        
    return outCurve
   

# This code defines what edges we take to compute the dGLI. Right now we take the edge before the last one in each side, as in the initial GLI paper
def subtractCircularBeg(total, ind):
    if ind == 0:
        return [total-3, total-2]
    else:
        return [ind-3, ind-2]


# edgesCurve1 contains a list of edges, that is, tuples {p1,p2} of 3D points
def dGLICoords(edgesCurve1):
    return dGLICoords2(edgesCurve1, edgesCurve1)

def dGLICoords2(edgesCurve1, edgesCurve2):
    numP1 = len(edgesCurve1) # it has to be 8
    numP2 = len(edgesCurve2) # it has to be 8

    # dGLIMatrix = []
    #dGLIMatrix = np.zeros((numP1, numP2), dtype = float)
    vector_res = []

    for i in range(numP1):
      for j in range(i, numP2):
        if i!=j:
            dgli=dGLI(edgesCurve1[i][0], edgesCurve1[i][1], edgesCurve2[j][0], edgesCurve2[j][1])
            vector_res.append(dgli)

    return vector_res


def dGLI(ap1, ap2, ap3, ap4):
    epsilon = 0.00001
    p1 = np.add(ap1 ,[0, 0, 0])
    p2 = np.add(ap2, [0, 0, epsilon])
    p3 = np.add(ap3, [0, 0, 0])
    p4 = np.add(ap4, [0, 0, epsilon])
# if we are evaluating the same segment
    if np.linalg.norm(np.subtract(ap1,ap3)) < 0.01 and np.linalg.norm(np.subtract(ap2,ap4)) < 0.01:
        ret = 0
    else:
        GLI = evalWritheTwoSegments(ap1, ap2, ap3, ap4)
        
        GLIPerturbed = evalWritheTwoSegments(p1, p2, p3, p4)
        

        ret = (GLIPerturbed - GLI) / epsilon

    if abs(ret) > 4.0:
        return np.sign(ret) * 4
    else:
        return ret

def evalWritheTwoSegments(p1, p2, p3, p4):
    n1 = np.cross(np.subtract(p3,p1), np.subtract(p4,p1)) / norm(np.cross(np.subtract(p3,p1), np.subtract(p4,p1)))
    n2 = np.cross(np.subtract(p4,p1), np.subtract(p4,p2)) / norm(np.cross(np.subtract(p4,p1), np.subtract(p4,p2)))
    n3 = np.cross(np.subtract(p4,p2), np.subtract(p3,p2)) / norm(np.cross(np.subtract(p4,p2), np.subtract(p3,p2)))
    n4 = np.cross(np.subtract(p3,p2), np.subtract(p3,p1)) / norm(np.cross(np.subtract(p3,p2), np.subtract(p3,p1)))
    sgn = np.sign(np.dot(np.cross(np.subtract(p4,p3),np.subtract(p2,p1)), np.subtract(p3,p1)))
    ret = np.arcsin(np.dot(n1,n2)) + np.arcsin(np.dot(n2,n3)) + np.arcsin(np.dot(n3,n4)) + np.arcsin(np.dot(n4,n1))
    return sgn*ret


***Validation test***

In [3]:
curve1=[[-0.275117, -1.22472, 0.782454], [-0.275234, -1.25103, 0.781838], [-0.275101, -1.27738, 0.781222], [-0.275021, -1.30368, 0.780606], [-0.274939, -1.32991, 0.779992], [-0.275092, -1.35622, 0.779376], [-0.275112, -1.38247, 0.778763], [-0.274996, -1.40869, 0.778149], [-0.274911, -1.43499, 0.777533], [-0.27483, -1.46128, 0.776918], [-0.274693, -1.48758, 0.776383], [-0.274582, -1.51387, 0.775688], [-0.274454, -1.54017, 0.775142], [-0.274411, -1.56646, 0.774458], [-0.274332, -1.59275, 0.773842], [-0.274237, -1.61917, 0.773224], [-0.273913, -1.64545, 0.772608], [-0.273668, -1.67197, 0.771988], [-0.27352, -1.69833, 0.771372], [-0.273452, -1.72462, 0.770811], [-0.247152, -1.72457, 0.770776], [-0.220774, -1.72464, 0.770792], [-0.194233, -1.72479, 0.770807], [-0.167959, -1.72517, 0.770816], [-0.141366, -1.72521, 0.770833], [-0.115029, -1.72532, 0.770849], [-0.0887752, -1.72523, 0.770869], [-0.0624425, -1.7252, 0.770888], [-0.0362156, -1.72511, 0.770907], [-0.00989175, -1.72516, 0.770926], [0.0163153, -1.72522, 0.770942], [0.0425979, -1.72504, 0.770964], [0.0688676, -1.725, 0.770983], [0.0951935, -1.7252, 0.770996], [0.121492, -1.72535, 0.771011], [0.147809, -1.7254, 0.771028], [0.174208, -1.72534, 0.771047], [0.200562, -1.72534, 0.771065], [0.22688, -1.72538, 0.771083], [0.227004, -1.69907, 0.771698], [0.226941, -1.67272, 0.772315], [0.227182, -1.64638, 0.772932], [0.227149, -1.62007, 0.773547], [0.227037, -1.59369, 0.774164], [0.227106, -1.56743, 0.77478], [0.227092, -1.54114, 0.775394], [0.22705, -1.51486, 0.776009], [0.226998, -1.48857, 0.776624], [0.226921, -1.46228, 0.77724], [0.226857, -1.43599, 0.777855], [0.226784, -1.40969, 0.77849], [0.226746, -1.38343, 0.779139], [0.226794, -1.35713, 0.7797], [0.226663, -1.33091, 0.780314], [0.226626, -1.30455, 0.78093], [0.226133, -1.27801, 0.781551], [0.225905, -1.25163, 0.782169], [0.225697, -1.22534, 0.782803], [0.19938, -1.2255, 0.782762], [0.173024, -1.22548, 0.782744], [0.146611, -1.22504, 0.782736], [0.120292, -1.22486, 0.782722], [0.0936924, -1.22471, 0.782707], [0.0673476, -1.22475, 0.782688], [0.0409484, -1.22486, 0.782668], [0.0146931, -1.22499, 0.782647], [-0.0116226, -1.22515, 0.782626], [-0.0379447, -1.2251, 0.782608], [-0.0642397, -1.225, 0.782592], [-0.0905873, -1.22497, 0.782575], [-0.117038, -1.22487, 0.782559], [-0.143311, -1.22465, 0.782546], [-0.169638, -1.2245, 0.782531], [-0.195966, -1.22439, 0.782516], [-0.22255, -1.22456, 0.782494], [-0.248787, -1.22467, 0.782473]]
curve2=[[-0.274013, -1.22362, 0.78248], [-0.274121, -1.24992, 0.781865], [-0.274277, -1.27628, 0.781248], [-0.274351, -1.30274, 0.780629], [-0.274399, -1.32903, 0.780013], [-0.274337, -1.3554, 0.779396], [-0.274296, -1.38176, 0.778779], [-0.274306, -1.40811, 0.778163], [-0.274257, -1.43443, 0.777547], [-0.274275, -1.46103, 0.776924], [-0.274277, -1.48735, 0.776308], [-0.274324, -1.51409, 0.775683], [-0.274294, -1.54041, 0.775067], [-0.274309, -1.56723, 0.774439], [-0.274228, -1.59355, 0.773823], [-0.274117, -1.6202, 0.773199], [-0.273742, -1.64651, 0.772584], [-0.27357, -1.67271, 0.771971], [-0.273591, -1.69908, 0.771354], [-0.273632, -1.72538, 0.770806], [-0.247339, -1.72536, 0.770757], [-0.220982, -1.72539, 0.770774], [-0.194607, -1.72555, 0.770789], [-0.168338, -1.72585, 0.7708], [-0.142027, -1.72584, 0.770818], [-0.115805, -1.72574, 0.770838], [-0.0895951, -1.72558, 0.77086], [-0.0633502, -1.72518, 0.770888], [-0.0371641, -1.72516, 0.770906], [-0.0108621, -1.72512, 0.770925], [0.0152077, -1.72523, 0.770941], [0.0414956, -1.72539, 0.770955], [0.0677782, -1.72545, 0.770971], [0.0940687, -1.72578, 0.770982], [0.120372, -1.72601, 0.770994], [0.146707, -1.72618, 0.771009], [0.173125, -1.72623, 0.771026], [0.199464, -1.72638, 0.771089], [0.225781, -1.72648, 0.771071], [0.225978, -1.70017, 0.771672], [0.225929, -1.67375, 0.77229], [0.226257, -1.64747, 0.772905], [0.22641, -1.62113, 0.773522], [0.226279, -1.59449, 0.774145], [0.226448, -1.56816, 0.774761], [0.226117, -1.54107, 0.775395], [0.225976, -1.51482, 0.778409], [0.22322, -1.48897, 0.787774], [0.217795, -1.46586, 0.799501], [0.203239, -1.44877, 0.814823], [0.179907, -1.44302, 0.825737], [0.160577, -1.45034, 0.809227], [0.136648, -1.44792, 0.798528], [0.112715, -1.45821, 0.802008], [0.0878899, -1.46119, 0.809629], [0.0622547, -1.46364, 0.814631], [0.0405122, -1.45877, 0.828698], [0.0212286, -1.44561, 0.84084], [0.00901499, -1.44389, 0.817439], [0.00570795, -1.42479, 0.79966], [0.00233644, -1.39887, 0.798553], [-0.00219762, -1.37313, 0.801654], [-0.00672734, -1.34741, 0.803741], [-0.0067696, -1.32132, 0.804368], [-0.0153184, -1.30246, 0.82066], [-0.0186663, -1.27743, 0.827653], [-0.0211709, -1.25201, 0.82139], [-0.0422448, -1.24106, 0.810026], [-0.0631711, -1.22996, 0.797863], [-0.0886693, -1.2263, 0.790357], [-0.115376, -1.225, 0.78659], [-0.141338, -1.22437, 0.782554], [-0.168229, -1.22403, 0.782544], [-0.194488, -1.22379, 0.782531], [-0.221338, -1.22369, 0.782515], [-0.247714, -1.22365, 0.782498]]

In [4]:
coordsdGLI1=[4, 0.157887, 0.21199, 0.110153, 0.0993557, 0.156534, 0.00452688, 0.00122104, 0.156315, 0.0982562, 0.109479, 0.210012, 0.157283, 4, 0.156497, 0.210565, 0.112167, 0.100889, 0.00163678, 0.156106,0.101049, 0.111878, 4, 0.158544, 0.210827, 0.00543083, 0.156991, 4]
coordsdGLI2=[4, 0.157766, 0.211115, 0.110596, 0.0995439, -0.00844612, 0.43422,0.00180441, 0.154916, 0.0986447, 0.109765, 0.0663872, 0.501821, 4, 0.155185, 0.20997, 0.205149, 0.295824, 0.000790318, 0.156102, 0.222728, 0.272104, 4, 0.632962, 0.122105, 0.592691, 0.0267658, -4]

In [5]:
np.subtract(getdGLICoords(curve2,20),coordsdGLI2)

array([ 0.00000000e+00, -7.42077762e-03, -2.86392515e-03, -8.98584216e-03,
       -6.70087500e-03, -1.44530528e-03, -6.01598058e-02,  2.58584185e-06,
        6.19962443e-06,  1.67558940e-05,  3.11568586e-06,  4.31539510e-05,
       -1.72805118e-05,  0.00000000e+00,  5.34579329e-05,  1.67061345e-05,
        4.84554496e-05,  2.96485786e-06,  2.80903744e-05, -1.94972331e-05,
        1.02811748e-05, -2.40118605e-05,  0.00000000e+00,  1.05625642e-05,
        4.27202940e-05, -5.77448635e-05,  2.53460572e-05,  0.00000000e+00])

In [6]:
np.subtract(getdGLICoords(curve1,20),coordsdGLI1)

array([ 0.00000000e+00, -6.70909851e-03, -2.28528248e-03, -8.80553778e-03,
       -6.57200450e-03, -1.84706875e-02, -9.96671119e-04, -4.19067314e-06,
        1.02640890e-05, -5.36111307e-06,  1.05842879e-05, -1.40534791e-05,
        4.17421837e-06,  0.00000000e+00, -2.18635520e-05,  8.42880493e-06,
       -1.37615926e-05, -2.50930516e-06, -8.42548915e-05, -2.61306155e-05,
       -2.40078060e-05, -1.20327106e-05,  0.00000000e+00, -1.51643627e-06,
        2.47290196e-06,  2.04432819e-06,  2.23256957e-06,  0.00000000e+00])

In [12]:
#Function to obtain the cloth border given a mesh of the cloth from the VR simulator.
def getSquaredBorder(mesh, sideSize):
    s1 = list(range(0, sideSize-1))
    s2 = [(i+1)*sideSize-1 for i in range(0, sideSize-1)]
    s3 = [sideSize*sideSize-i-1 for i in range(0, sideSize-1)]
    s4 = list(reversed([(i+1)*sideSize for i in range(0, sideSize-1)]))
    borderInd = s1 + s2 + s3 + s4
    return [mesh[i] for i in borderInd]

In [10]:
testMesh=[[-0.273914, -1.22369, 0.782479], [-0.274051, -1.25, 0.781863], [-0.274196, -1.27633, 0.781247], [-0.274297, -1.30279, 0.780627], [-0.274317, -1.32902, 0.780014], [-0.274223, -1.35539, 0.779397], [-0.274104, -1.3817, 0.778781], [-0.274083, -1.40807, 0.778164], [-0.273951, -1.43438, 0.777548], [-0.273931, -1.46098, 0.776926], [-0.273853, -1.4873, 0.77631], [-0.273808, -1.51399, 0.775685], [-0.273758, -1.54031, 0.775069], [-0.273698, -1.56705, 0.774444], [-0.273633, -1.59337, 0.773828], [-0.273478, -1.6201, 0.773202], [-0.273043, -1.64641, 0.772587], [-0.272816, -1.67277, 0.77197], [-0.272773, -1.69908, 0.771373], [-0.272628, -1.72538, 0.770739], [-0.247594, -1.22367, 0.782497], [-0.247719, -1.24998, 0.781882], [-0.247882, -1.27631, 0.781265], [-0.24797, -1.30269, 0.780648], [-0.248002, -1.329, 0.780032], [-0.247797, -1.35529, 0.779417], [-0.247784, -1.38161, 0.778801], [-0.247623, -1.40812, 0.778181], [-0.24763, -1.43449, 0.777564], [-0.2475, -1.46109, 0.776941], [-0.247533, -1.48746, 0.776324], [-0.247409, -1.51405, 0.775702], [-0.247438, -1.54044, 0.775085], [-0.247324, -1.56703, 0.774462], [-0.247259, -1.59333, 0.773847], [-0.247072, -1.61974, 0.773229], [-0.246699, -1.64611, 0.772612], [-0.246488, -1.67265, 0.771991], [-0.246379, -1.69891, 0.771377], [-0.246322, -1.72528, 0.770777], [-0.22127, -1.22368, 0.782515], [-0.221363, -1.24998, 0.7819], [-0.221607, -1.27628, 0.781284], [-0.221687, -1.30256, 0.780668], [-0.221658, -1.3289, 0.780053], [-0.221474, -1.35535, 0.779434], [-0.221463, -1.38176, 0.778816], [-0.221304, -1.40829, 0.778195], [-0.221311, -1.4347, 0.777577], [-0.22118, -1.46125, 0.776956], [-0.221216, -1.48766, 0.776338], [-0.22109, -1.5142, 0.775717], [-0.22112, -1.54063, 0.775098], [-0.221003, -1.56703, 0.77448], [-0.22096, -1.59332, 0.773865], [-0.220753, -1.61963, 0.77325], [-0.220411, -1.64614, 0.772629], [-0.220147, -1.67261, 0.77201], [-0.220128, -1.69895, 0.771394], [-0.219964, -1.72528, 0.770778], [-0.194808, -1.22371, 0.782533], [-0.194961, -1.24997, 0.781918], [-0.195235, -1.27632, 0.781301], [-0.195207, -1.3028, 0.780681], [-0.195256, -1.32912, 0.780066], [-0.195061, -1.35563, 0.779445], [-0.195089, -1.38196, 0.778829], [-0.194892, -1.4085, 0.778208], [-0.19494, -1.43484, 0.777592], [-0.194747, -1.4614, 0.77697], [-0.194804, -1.48774, 0.776354], [-0.194628, -1.51428, 0.775733], [-0.194676, -1.54062, 0.775117], [-0.194501, -1.56713, 0.774496], [-0.194472, -1.59337, 0.773882], [-0.194275, -1.61984, 0.773263], [-0.194104, -1.64609, 0.772649], [-0.193637, -1.67271, 0.772026], [-0.193671, -1.69902, 0.77141], [-0.193535, -1.72543, 0.770792], [-0.168466, -1.2239, 0.782546], [-0.168692, -1.25021, 0.78193], [-0.168909, -1.27653, 0.781314], [-0.168888, -1.30299, 0.780695], [-0.168931, -1.32931, 0.780079], [-0.168741, -1.35581, 0.779459], [-0.16877, -1.38213, 0.778843], [-0.168572, -1.40868, 0.778222], [-0.16862, -1.435, 0.777606], [-0.168427, -1.46156, 0.776985], [-0.168485, -1.48788, 0.776369], [-0.168308, -1.51441, 0.775748], [-0.168357, -1.54073, 0.775132], [-0.168145, -1.56716, 0.774514], [-0.16816, -1.59349, 0.773897], [-0.167943, -1.61984, 0.773281], [-0.167847, -1.64625, 0.772663], [-0.167316, -1.67285, 0.772041], [-0.167351, -1.69921, 0.771424], [-0.167214, -1.72562, 0.770806], [-0.142184, -1.22414, 0.782559], [-0.142315, -1.25045, 0.781943], [-0.142488, -1.27675, 0.781327], [-0.142421, -1.30313, 0.78071], [-0.142485, -1.32947, 0.780094], [-0.142304, -1.35596, 0.779474], [-0.142308, -1.38228, 0.778858], [-0.142108, -1.40877, 0.778238], [-0.142128, -1.43509, 0.777622], [-0.14194, -1.46159, 0.777002], [-0.141962, -1.48791, 0.776386], [-0.141793, -1.51439, 0.775767], [-0.141806, -1.54071, 0.775151], [-0.141649, -1.56719, 0.774531], [-0.141617, -1.59351, 0.773915], [-0.141498, -1.61997, 0.773296], [-0.141411, -1.64627, 0.772681], [-0.140898, -1.67284, 0.772059], [-0.140848, -1.69915, 0.771444], [-0.140776, -1.72553, 0.770826], [-0.115901, -1.22439, 0.782571], [-0.115963, -1.2507, 0.781955], [-0.116147, -1.277, 0.78134], [-0.116101, -1.30331, 0.780724], [-0.116165, -1.32963, 0.780108], [-0.115985, -1.35609, 0.779489], [-0.115988, -1.38241, 0.778873], [-0.115789, -1.4089, 0.778253], [-0.115808, -1.43522, 0.777637], [-0.115613, -1.46172, 0.777017], [-0.115642, -1.48803, 0.776402], [-0.115475, -1.5145, 0.775782], [-0.115485, -1.54082, 0.775166], [-0.11531, -1.56728, 0.774547], [-0.115297, -1.5936, 0.773932], [-0.115173, -1.62003, 0.773313], [-0.115074, -1.6463, 0.772698], [-0.114652, -1.67282, 0.772078], [-0.11459, -1.69915, 0.771462], [-0.114538, -1.72547, 0.770846], [-0.0896027, -1.22453, 0.782586], [-0.089751, -1.25084, 0.78197], [-0.0897981, -1.27715, 0.781354], [-0.0897432, -1.30354, 0.780737], [-0.0896942, -1.32985, 0.780121], [-0.0895016, -1.35622, 0.779504], [-0.0894726, -1.38254, 0.778888], [-0.0892611, -1.4089, 0.778271], [-0.0892455, -1.43522, 0.777656], [-0.0890655, -1.46168, 0.777037], [-0.0890555, -1.488, 0.776421], [-0.0889186, -1.51443, 0.775802], [-0.08887, -1.54075, 0.775186], [-0.088878, -1.56723, 0.774567], [-0.0888196, -1.59355, 0.773951], [-0.0887829, -1.61988, 0.773334], [-0.0885898, -1.64624, 0.772718], [-0.0883028, -1.67259, 0.772101], [-0.0882613, -1.69895, 0.771484], [-0.0883089, -1.72527, 0.770868], [-0.0633076, -1.22457, 0.782603], [-0.0634785, -1.25088, 0.781987], [-0.063511, -1.27718, 0.781372], [-0.0634111, -1.30364, 0.780752], [-0.0633768, -1.33001, 0.780135], [-0.0631816, -1.35628, 0.779521], [-0.0631512, -1.38261, 0.778905], [-0.0629428, -1.409, 0.778287], [-0.0629254, -1.43532, 0.777671], [-0.0627456, -1.46176, 0.777053], [-0.0627351, -1.48808, 0.776437], [-0.0625736, -1.51448, 0.775819], [-0.0625494, -1.5408, 0.775203], [-0.0625565, -1.56711, 0.774587], [-0.0624973, -1.59334, 0.773974], [-0.0624225, -1.61965, 0.773358], [-0.0622775, -1.64596, 0.772742], [-0.0620303, -1.67246, 0.772122], [-0.0620538, -1.6988, 0.771506], [-0.0620184, -1.72515, 0.770889], [-0.0370466, -1.22466, 0.782618], [-0.0371663, -1.25099, 0.782003], [-0.0371986, -1.27728, 0.781387], [-0.0369985, -1.30358, 0.780772], [-0.036949, -1.32997, 0.780154], [-0.0366592, -1.3564, 0.779536], [-0.0365926, -1.38271, 0.778921], [-0.0363641, -1.40901, 0.778305], [-0.0363252, -1.43534, 0.777689], [-0.0361672, -1.46167, 0.777073], [-0.0361066, -1.48799, 0.776457], [-0.036148, -1.51433, 0.775841], [-0.0360595, -1.54062, 0.775226], [-0.0361499, -1.56687, 0.774611], [-0.0360449, -1.59319, 0.773995], [-0.0360058, -1.61958, 0.773378], [-0.035959, -1.64593, 0.772761], [-0.0357801, -1.67238, 0.772142], [-0.0357958, -1.69869, 0.771526], [-0.0358352, -1.72501, 0.770911], [-0.0107157, -1.22467, 0.782638], [-0.0108109, -1.25098, 0.782021], [-0.0108691, -1.27726, 0.781406], [-0.0106838, -1.30363, 0.780789], [-0.0106294, -1.32994, 0.780173], [-0.0103407, -1.35643, 0.779554], [-0.0102742, -1.38274, 0.778938], [-0.0100429, -1.40901, 0.778323], [-0.010004, -1.43533, 0.777707], [-0.00983959, -1.46173, 0.77709], [-0.00978732, -1.48805, 0.776474], [-0.00982988, -1.5144, 0.775857], [-0.00974056, -1.54062, 0.775244], [-0.00979453, -1.56686, 0.774629], [-0.00972751, -1.59326, 0.774012], [-0.00968596, -1.61966, 0.773394], [-0.00963986, -1.6461, 0.772775], [-0.00946009, -1.67241, 0.77216], [-0.00947818, -1.69865, 0.771546], [-0.00951019, -1.72502, 0.770929], [0.0155433, -1.22447, 0.78266], [0.0154682, -1.25077, 0.782044], [0.015421, -1.27707, 0.781429], [0.0157433, -1.30349, 0.780811], [0.0158686, -1.32984, 0.780194], [0.0162479, -1.35616, 0.779578], [0.0163276, -1.38248, 0.778962], [0.0165732, -1.40892, 0.778344], [0.016637, -1.43524, 0.777728], [0.016685, -1.46168, 0.777109], [0.0166674, -1.488, 0.776493], [0.0166994, -1.51436, 0.775876], [0.0166088, -1.54065, 0.775261], [0.0166605, -1.56696, 0.774645], [0.0166731, -1.59326, 0.77403], [0.0166752, -1.61975, 0.77341], [0.0167221, -1.64609, 0.772794], [0.0167804, -1.6725, 0.772176], [0.0167154, -1.69882, 0.77156], [0.0166362, -1.72513, 0.770944], [0.0418419, -1.22432, 0.782681], [0.0417968, -1.25064, 0.782065], [0.0417417, -1.27696, 0.781449], [0.0420636, -1.30334, 0.780832], [0.0421894, -1.32969, 0.780216], [0.042568, -1.35623, 0.779595], [0.0426472, -1.38255, 0.778979], [0.042893, -1.40903, 0.778359], [0.0429567, -1.43535, 0.777743], [0.0430048, -1.46174, 0.777126], [0.0429449, -1.48805, 0.77651], [0.0430194, -1.51438, 0.775894], [0.0429625, -1.54069, 0.775278], [0.0430175, -1.567, 0.774662], [0.0430315, -1.5933, 0.774047], [0.04301, -1.61965, 0.77343], [0.0430505, -1.64596, 0.772815], [0.0430674, -1.67233, 0.772198], [0.0429717, -1.69859, 0.771583], [0.0429129, -1.72495, 0.770966], [0.0681919, -1.2242, 0.782702], [0.068156, -1.2505, 0.782087], [0.0682403, -1.2768, 0.781471], [0.0686152, -1.30334, 0.78085], [0.0687557, -1.32967, 0.780234], [0.0691781, -1.35623, 0.779613], [0.0690788, -1.38258, 0.778996], [0.0693974, -1.40904, 0.778377], [0.0692824, -1.43535, 0.777761], [0.0693045, -1.46175, 0.777144], [0.0691885, -1.48807, 0.776528], [0.0692901, -1.51438, 0.775912], [0.0691762, -1.54071, 0.775296], [0.0694588, -1.56705, 0.774679], [0.0693506, -1.59336, 0.774064], [0.069431, -1.61969, 0.773448], [0.0693974, -1.64598, 0.772832], [0.0693578, -1.67232, 0.772216], [0.0692491, -1.69861, 0.771601], [0.0691842, -1.72494, 0.770984], [0.0945017, -1.22421, 0.78272], [0.0944992, -1.2506, 0.782102], [0.0945371, -1.2769, 0.781487], [0.094934, -1.30348, 0.780865], [0.0950666, -1.32981, 0.780249], [0.0954978, -1.35638, 0.779627], [0.0953908, -1.38272, 0.779011], [0.0957159, -1.40918, 0.778392], [0.0955586, -1.4355, 0.777776], [0.0955911, -1.46187, 0.777159], [0.0954911, -1.48818, 0.776543], [0.0955398, -1.5145, 0.775927], [0.0954521, -1.54081, 0.775311], [0.0957795, -1.56714, 0.774696], [0.0956658, -1.59346, 0.774079], [0.0958011, -1.61978, 0.773464], [0.0957376, -1.64618, 0.772846], [0.0956473, -1.67252, 0.772229], [0.0955393, -1.69883, 0.771614], [0.0954548, -1.72514, 0.770998], [0.121098, -1.22439, 0.782734], [0.121008, -1.25083, 0.782115], [0.120963, -1.27715, 0.781499], [0.121423, -1.30381, 0.780876], [0.121446, -1.33012, 0.78026], [0.12202, -1.35655, 0.779642], [0.12174, -1.38284, 0.779026], [0.122023, -1.40932, 0.778407], [0.121823, -1.43568, 0.77779], [0.121878, -1.46202, 0.777173], [0.121838, -1.48833, 0.776558], [0.121932, -1.51463, 0.775942], [0.121914, -1.54095, 0.775326], [0.122139, -1.56728, 0.77471], [0.122015, -1.59363, 0.774094], [0.122113, -1.61997, 0.773477], [0.122174, -1.64634, 0.77286], [0.121892, -1.67267, 0.772244], [0.121828, -1.69897, 0.771628], [0.121761, -1.72529, 0.771012], [0.147417, -1.2247, 0.782745], [0.147324, -1.25106, 0.782128], [0.147347, -1.27742, 0.781511], [0.147742, -1.30405, 0.780888], [0.147733, -1.33036, 0.780272], [0.148338, -1.35673, 0.779656], [0.148033, -1.38305, 0.77904], [0.14826, -1.40949, 0.778421], [0.148128, -1.43585, 0.777804], [0.148193, -1.46214, 0.777189], [0.148158, -1.48845, 0.776573], [0.14823, -1.51476, 0.775957], [0.148211, -1.54107, 0.775342], [0.148401, -1.56748, 0.774724], [0.148316, -1.59373, 0.774109], [0.148391, -1.62014, 0.773491], [0.148493, -1.64646, 0.772876], [0.148135, -1.67274, 0.77226], [0.148113, -1.69903, 0.771645], [0.148074, -1.72536, 0.771029], [0.173816, -1.22517, 0.782752], [0.173874, -1.25149, 0.782136], [0.173901, -1.27781, 0.78152], [0.174517, -1.30428, 0.780901], [0.174416, -1.3306, 0.780285], [0.174735, -1.357, 0.779667], [0.174526, -1.3833, 0.779052], [0.174579, -1.40963, 0.778436], [0.174637, -1.43593, 0.77782], [0.174646, -1.46221, 0.777205], [0.17466, -1.48851, 0.77659], [0.174706, -1.51484, 0.775974], [0.174772, -1.54116, 0.775358], [0.174671, -1.56746, 0.774742], [0.174642, -1.59378, 0.774126], [0.174665, -1.62014, 0.773509], [0.17476, -1.64643, 0.772894], [0.174476, -1.67268, 0.77228], [0.174512, -1.69897, 0.771665], [0.174474, -1.72531, 0.771048], [0.200094, -1.22524, 0.782768], [0.200252, -1.25159, 0.782151], [0.200277, -1.27785, 0.781537], [0.2008, -1.30441, 0.780916], [0.200758, -1.33071, 0.780301], [0.20103, -1.35714, 0.779682], [0.200863, -1.38343, 0.779067], [0.200952, -1.40973, 0.778452], [0.200966, -1.43603, 0.777836], [0.201009, -1.46233, 0.777221], [0.201027, -1.48861, 0.776606], [0.201048, -1.51488, 0.775991], [0.201061, -1.54113, 0.775377], [0.201059, -1.56738, 0.774769], [0.200917, -1.59367, 0.774147], [0.201, -1.62, 0.773531], [0.201049, -1.64633, 0.772915], [0.200807, -1.67262, 0.772299], [0.200916, -1.69896, 0.771683], [0.200789, -1.72529, 0.771067], [0.226438, -1.22515, 0.782806], [0.226629, -1.25145, 0.782173], [0.226735, -1.2778, 0.781557], [0.227215, -1.30438, 0.780935], [0.227173, -1.33068, 0.780319], [0.227363, -1.35707, 0.779702], [0.227267, -1.38336, 0.779103], [0.227273, -1.40964, 0.778472], [0.227287, -1.43594, 0.777857], [0.227339, -1.46224, 0.777297], [0.227369, -1.48854, 0.776625], [0.227395, -1.51483, 0.77601], [0.227387, -1.54113, 0.775395], [0.227365, -1.56741, 0.77478], [0.227243, -1.5937, 0.774164], [0.227319, -1.62, 0.773549], [0.227367, -1.64632, 0.772933], [0.227124, -1.67268, 0.772316], [0.227213, -1.69897, 0.771701], [0.227115, -1.72529, 0.771112]]
testBorder=[[-0.273914, -1.22369, 0.782479], [-0.274051, -1.25, 0.781863], [-0.274196, -1.27633, 0.781247], [-0.274297, -1.30279, 0.780627], [-0.274317, -1.32902, 0.780014], [-0.274223, -1.35539, 0.779397], [-0.274104, -1.3817, 0.778781], [-0.274083, -1.40807, 0.778164], [-0.273951, -1.43438, 0.777548], [-0.273931, -1.46098, 0.776926], [-0.273853, -1.4873, 0.77631], [-0.273808, -1.51399, 0.775685], [-0.273758, -1.54031, 0.775069], [-0.273698, -1.56705, 0.774444], [-0.273633, -1.59337, 0.773828], [-0.273478, -1.6201, 0.773202], [-0.273043, -1.64641, 0.772587], [-0.272816, -1.67277, 0.77197], [-0.272773, -1.69908, 0.771373], [-0.272628, -1.72538, 0.770739], [-0.246322, -1.72528, 0.770777], [-0.219964, -1.72528, 0.770778], [-0.193535, -1.72543, 0.770792], [-0.167214, -1.72562, 0.770806], [-0.140776, -1.72553, 0.770826], [-0.114538, -1.72547, 0.770846], [-0.0883089, -1.72527, 0.770868], [-0.0620184, -1.72515, 0.770889], [-0.0358352, -1.72501, 0.770911], [-0.00951019, -1.72502, 0.770929], [0.0166362, -1.72513, 0.770944], [0.0429129, -1.72495, 0.770966], [0.0691842, -1.72494, 0.770984], [0.0954548, -1.72514, 0.770998], [0.121761, -1.72529, 0.771012], [0.148074, -1.72536, 0.771029], [0.174474, -1.72531, 0.771048], [0.200789, -1.72529, 0.771067], [0.227115, -1.72529, 0.771112], [0.227213, -1.69897, 0.771701], [0.227124, -1.67268, 0.772316], [0.227367, -1.64632, 0.772933], [0.227319, -1.62, 0.773549], [0.227243, -1.5937, 0.774164], [0.227365, -1.56741, 0.77478], [0.227387, -1.54113, 0.775395], [0.227395, -1.51483, 0.77601], [0.227369, -1.48854, 0.776625], [0.227339, -1.46224, 0.777297], [0.227287, -1.43594, 0.777857], [0.227273, -1.40964, 0.778472], [0.227267, -1.38336, 0.779103], [0.227363, -1.35707, 0.779702], [0.227173, -1.33068, 0.780319], [0.227215, -1.30438, 0.780935], [0.226735, -1.2778, 0.781557], [0.226629, -1.25145, 0.782173], [0.226438, -1.22515, 0.782806], [0.200094, -1.22524, 0.782768], [0.173816, -1.22517, 0.782752], [0.147417, -1.2247, 0.782745], [0.121098, -1.22439, 0.782734], [0.0945017, -1.22421, 0.78272], [0.0681919, -1.2242, 0.782702], [0.0418419, -1.22432, 0.782681], [0.0155433, -1.22447, 0.78266], [-0.0107157, -1.22467, 0.782638], [-0.0370466, -1.22466, 0.782618], [-0.0633076, -1.22457, 0.782603], [-0.0896027, -1.22453, 0.782586], [-0.115901, -1.22439, 0.782571], [-0.142184, -1.22414, 0.782559], [-0.168466, -1.2239, 0.782546], [-0.194808, -1.22371, 0.782533], [-0.22127, -1.22368, 0.782515], [-0.247594, -1.22367, 0.782497]]

In [13]:
resBorder=getSquaredBorder(testMesh,20)

In [14]:
np.subtract(testBorder,resBorder)

array([[0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0., 0.],
       [0., 0